## Homework: Search Evaluation

In this homework, we will evaluate the results of vector
search.

> It's possible that your answers won't match exactly. If it's the case, select the closest one.


## Required libraries

We will use minsearch and Qdrant. Make sure you have the most up-to-date versions:

```bash
pip install -U minsearch qdrant_client
``` 

minsearch should be at least 0.0.4.



## Evaluation data

For this homework, we will use the same dataset we generated
in the videos.

In [1]:
import requests
import pandas as pd

url_prefix = 'https://raw.githubusercontent.com/DataTalksClub/llm-zoomcamp/main/03-evaluation/'
docs_url = url_prefix + 'search_evaluation/documents-with-ids.json'
documents = requests.get(docs_url).json()

ground_truth_url = url_prefix + 'search_evaluation/ground-truth-data.csv'
df_ground_truth = pd.read_csv(ground_truth_url)
ground_truth = df_ground_truth.to_dict(orient='records')

In [2]:
from tqdm.auto import tqdm

def hit_rate(relevance_total):
    cnt = 0

    for line in relevance_total:
        if True in line:
            cnt = cnt + 1

    return cnt / len(relevance_total)

def mrr(relevance_total):
    total_score = 0.0

    for line in relevance_total:
        for rank in range(len(line)):
            if line[rank] == True:
                total_score = total_score + 1 / (rank + 1)

    return total_score / len(relevance_total)

def evaluate(ground_truth, search_function):
    relevance_total = []

    for q in tqdm(ground_truth):
        doc_id = q['document']
        results = search_function(q)
        relevance = [d['id'] == doc_id for d in results]
        relevance_total.append(relevance)

    return {
        'hit_rate': hit_rate(relevance_total),
        'mrr': mrr(relevance_total),
    }

/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Q1. Minsearch text

Now let's evaluate our usual minsearch approach, but tweak
the parameters. Let's use the following boosting 
params:

```python
boost = {'question': 1.5, 'section': 0.1}
```

What's the hitrate for this approach?

* 0.64
* 0.74
* 0.84
* 0.94


In [3]:
import minsearch

index = minsearch.Index(
    text_fields=["question", "text", "section"],
    keyword_fields=["course", "id"]
)

index.fit(documents)

In [4]:
def minsearch_search(query, course):
    boost = {'question': 1.5, 'section': 0.1}

    results = index.search(
        query=query,
        filter_dict={'course': course},
        boost_dict=boost,
        num_results=5
    )

    return results

In [5]:
evaluate(ground_truth, lambda q: minsearch_search(q['question'], q['course']))

100%|██████████| 4627/4627 [00:04<00:00, 1048.41it/s]


{'hit_rate': 0.848714069591528, 'mrr': 0.7288235717887772}

## Embeddings 

The latest version of minsearch also supports vector search. 
We will use it:

```python
from minsearch import VectorSearch
```

We will also use TF-IDF and Singular Value Decomposition to 
create embeddings from texts. You can refer to our
["Create Your Own Search Engine" workshop](https://github.com/alexeygrigorev/build-your-own-search-engine)
if you want to know more about it.

```python
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline
```

Let's create embeddings for the "question" field:

```python
texts = []

for doc in documents:
    t = doc['question']
    texts.append(t)

pipeline = make_pipeline(
    TfidfVectorizer(min_df=3),
    TruncatedSVD(n_components=128, random_state=1)
)
X = pipeline.fit_transform(texts)
```

## Q2. Vector search for question

Now let's index these embeddings with minsearch:

```python
vindex = VectorSearch(keyword_fields={'course'})
vindex.fit(X, documents)
```

Evaluate this seach method. What's MRR for it?

- 0.25
- 0.35
- 0.45
- 0.55

In [6]:
from minsearch import VectorSearch

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline

In [ ]:
texts = []

for doc in documents:
    t = doc['question']
    texts.append(t)

pipeline = make_pipeline(
    TfidfVectorizer(min_df=3),
    TruncatedSVD(n_components=128, random_state=1)
)
X = pipeline.fit_transform(texts)

In [9]:
vindex = VectorSearch(keyword_fields={'course'})
vindex.fit(X, documents)

In [59]:
def vector_search(query, course, vindex, pipeline):
    return vindex.search(
            query_vector=pipeline.transform([query]), 
            filter_dict={'course': course}, 
            num_results=5
            )

In [60]:
evaluate(ground_truth, lambda q: vector_search(q['question'], q['course'], vindex, pipeline))

  0%|          | 0/4627 [00:00<?, ?it/s]/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/cod

{'hit_rate': 0.48195374972984656, 'mrr': 0.3573085512571141}

Q3. Vector search for question and answer

In [61]:

texts = []

for doc in documents:
    t = doc['question'] + ' ' + doc['text']
    texts.append(t)

pipeline_q3 = make_pipeline(
    TfidfVectorizer(min_df=3),
    TruncatedSVD(n_components=128, random_state=1)
)
X = pipeline_q3.fit_transform(texts)


vindex_q3 = VectorSearch(keyword_fields={'course'})
vindex_q3.fit(X, documents)

/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:590: RuntimeWarning: divide by zero encountered in matmul
  U = Q @ Uhat
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:590: RuntimeWarning: overflow encountered in matmul
  U = Q @ Uhat
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:590: RuntimeWarning: invalid value encountered in matmul
  U = Q @ Uhat


In [62]:

evaluate(ground_truth, lambda q: vector_search(q['question'], q['course'], vindex_q3, pipeline_q3))

  0%|          | 0/4627 [00:00<?, ?it/s]/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: overflow encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: invalid value encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:203: RuntimeWarning: divide by zero encountered in matmul
  ret = a @ b
/Users/robertusprimusanto/Documents/cod

{'hit_rate': 0.8210503566025502, 'mrr': 0.6717347453353508}

Q4. Qdrant

In [73]:

from qdrant_client import QdrantClient, models

client = QdrantClient("http://localhost:6333")

model = "jinaai/jina-embeddings-v2-small-en"

client.set_model(model)

In [74]:
collection_name = "hmworkq4"

#client.delete_collection(collection_name=collection_name)

client.create_collection(
    collection_name=collection_name,
    vectors_config=models.VectorParams(
        size=512,
        distance=models.Distance.COSINE
    )
)

True

In [75]:

client.create_payload_index(
    collection_name=collection_name,
    field_name="course",
    field_schema="keyword"
)

UpdateResult(operation_id=1, status=<UpdateStatus.COMPLETED: 'completed'>)

In [76]:
points = []
id = 0

for doc in documents:
  point = models.PointStruct(
    id=id,
    vector=models.Document(text=doc['question'] + ' ' + doc['text'], model=model),
    payload={
      "text": doc['text'],
      "section": doc['section'],
      "course": doc['course'],
      "question": doc['question'],
      "id": doc['id']
    }
  )
  points.append(point)

  id += 1

In [77]:

# takes some time
client.upsert(
    collection_name=collection_name,
    points=points
)

UpdateResult(operation_id=2, status=<UpdateStatus.COMPLETED: 'completed'>)

In [78]:

def qd_search(query, course, limit=5):
    q_points = client.query_points(
                    collection_name=collection_name,
                    query=models.Document(text=query, model=model),
                    limit=limit,
                    with_payload=True,
                    query_filter=models.Filter(
                                    must=[
                                        models.FieldCondition(
                                        key="course",
                                        match=models.MatchValue(value=course)
                                        )
                                    ])
                     )
    #return query_points
    results = [point.payload for point in q_points.points]
    return results

In [80]:
evaluate(ground_truth, lambda q: qd_search(q['question'], q['course']))

100%|██████████| 4627/4627 [00:39<00:00, 118.28it/s]


{'hit_rate': 0.9299762264966501, 'mrr': 0.8517722066133576}

Q5. Cosine simiarity

In [81]:
def cosine(u, v):
    u_norm = np.sqrt(u.dot(u))
    v_norm = np.sqrt(v.dot(v))
    return u.dot(v) / (u_norm * v_norm)

In [82]:
results_url = url_prefix + 'rag_evaluation/data/results-gpt4o-mini.csv'
df_results = pd.read_csv(results_url)

In [83]:
df_results.head()

answer_llm  \
0  You can sign up for the course by visiting the...   
1  You can sign up using the link provided in the...   
2  Yes, there is an FAQ for the Machine Learning ...   
3  The context does not provide any specific info...   
4  To structure your questions and answers for th...   

                                         answer_orig  document  \
0  Machine Learning Zoomcamp FAQ\nThe purpose of ...  0227b872   
1  Machine Learning Zoomcamp FAQ\nThe purpose of ...  0227b872   
2  Machine Learning Zoomcamp FAQ\nThe purpose of ...  0227b872   
3  Machine Learning Zoomcamp FAQ\nThe purpose of ...  0227b872   
4  Machine Learning Zoomcamp FAQ\nThe purpose of ...  0227b872   

                                            question  \
0                Where can I sign up for the course?   
1                 Can you provide a link to sign up?   
2  Is there an FAQ for this Machine Learning course?   
3  Does this course have a GitHub repository for ...   
4  How can I structure my questions and answers f...   

                      course  
0  machine-learning-zoomcamp  
1  machine-learning-zoomcamp  
2  machine-learning-zoomcamp  
3  machine-learning-zoomcamp  
4  machine-learning-zoomcamp

In [84]:

pipeline_q5 = make_pipeline(
    TfidfVectorizer(min_df=3),
    TruncatedSVD(n_components=128, random_state=1)
)

In [85]:

pipeline_q5.fit(df_results.answer_llm + ' ' + df_results.answer_orig + ' ' + df_results.question)


/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:590: RuntimeWarning: divide by zero encountered in matmul
  U = Q @ Uhat
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:590: RuntimeWarning: overflow encountered in matmul
  U = Q @ Uhat
/Users/robertusprimusanto/Documents/code/dataTalksClub/llmzoomcamp-202506/homework-llmzoomcamp-2025/.venv/lib/python3.13/site-packages/sklearn/utils/extmath.py:590: RuntimeWarning: invalid value encountered in matmul
  U = Q @ Uhat


Pipeline(steps=[('tfidfvectorizer', TfidfVectorizer(min_df=3)),
                ('truncatedsvd',
                 TruncatedSVD(n_components=128, random_state=1))])

In [87]:

v_llm = pipeline_q5.transform(df_results.answer_llm)
v_orig = pipeline_q5.transform(df_results.answer_orig)

In [90]:
import numpy as np

In [93]:

similarities = []
for u, v in zip(v_llm, v_orig):
    similarities.append(cosine(u, v))

In [95]:

result = np.array(similarities)
print(result.mean().round(2))

0.84


Q6. Rouge

In [96]:
!pip install rouge

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [97]:
from rouge import Rouge
rouge_scorer = Rouge()

r = df_results.iloc[10]
scores = rouge_scorer.get_scores(r.answer_llm, r.answer_orig)[0]
scores

{'rouge-1': {'r': 0.45454545454545453,
  'p': 0.45454545454545453,
  'f': 0.45454544954545456},
 'rouge-2': {'r': 0.21621621621621623,
  'p': 0.21621621621621623,
  'f': 0.21621621121621637},
 'rouge-l': {'r': 0.3939393939393939,
  'p': 0.3939393939393939,
  'f': 0.393939388939394}}

In [ ]:

f1 = []

results = df_results.to_dict(orient='records')

for r in results:
  scores = rouge_scorer.get_scores(r["answer_llm"], r["answer_orig"])[0]
  r1_f1 = scores["rouge-1"]["f"]
  f1.append(r1_f1)


In [101]:
print(np.array(f1).mean().round(2))

0.35
